In [1]:
import findspark
findspark.init()
findspark.find()
import pyspark
from pyspark.sql import SparkSession
import pyspark.sql.functions as f

from pyspark.sql.functions import *
from pyspark.sql.types import *
from pyspark.context import SparkContext
from pyspark.sql.session import SparkSession
from pyspark.ml.feature import Tokenizer
from pyspark.ml.feature import StopWordsRemover
from pyspark.sql.functions import col,from_json
from pyspark.sql.types import StructType,StructField, StringType
spark = SparkSession.builder \
    .master('local[*]') \
    .config("spark.driver.memory", "15g") \
    .config("spark.driver.maxResultSize", "5g")\
    .config('spark.executor.instances', 4)\
    .config('spark.executor.cores', 4)\
    .config('spark.executor.memory', '10g')\
    .config('spark.driver.memory', '15g')\
    .config('spark.memory.offHeap.enabled', True)\
    .config('spark.memory.offHeap.size', '20g')\
    .appName('twitter-data') \
    .getOrCreate()
sc = spark.sparkContext



In [3]:
txt = sc.textFile("twitter_small.txt",10).map(lambda x: x.split('": '))
txt.collect()

[['{"created_at',
  '"Fri May 29 15:38:52 +0000 2020", "id',
  '1266393580223987713, "id_str',
  '"1266393580223987713", "full_text',
  '"RT @Desiree_Laverne: #MyBeautifulAfrica....\\u2764\\nAardwolf.. https://t.co/9C7MjkQaIp", "truncated',
  'false, "display_text_range',
  '[0, 79], "entities',
  '{"hashtags',
  '[{"text',
  '"MyBeautifulAfrica", "indices',
  '[21, 39]}], "symbols',
  '[], "user_mentions',
  '[{"screen_name',
  '"Desiree_Laverne", "name',
  '"Desiree_Laverne", "id',
  '2314937901, "id_str',
  '"2314937901", "indices',
  '[3, 19]}], "urls',
  '[], "media',
  '[{"id',
  '1266286817315176450, "id_str',
  '"1266286817315176450", "indices',
  '[56, 79], "media_url',
  '"http://pbs.twimg.com/media/EZLBJrnUwAI9IbT.jpg", "media_url_https',
  '"https://pbs.twimg.com/media/EZLBJrnUwAI9IbT.jpg", "url',
  '"https://t.co/9C7MjkQaIp", "display_url',
  '"pic.twitter.com/9C7MjkQaIp", "expanded_url',
  '"https://twitter.com/Desiree_Laverne/status/1266286830116200448/photo/1", "type',


In [4]:
rdd=txt.map(lambda x: (x[1], x[4])).distinct()


In [5]:
deptSchema = StructType([       
    StructField('Date', StringType(), True),
    StructField('Text', StringType(), True)
])

In [6]:
DF1 = spark.createDataFrame(rdd, schema = deptSchema)
DF1.show()


+--------------------+--------------------+
|                Date|                Text|
+--------------------+--------------------+
|"Fri May 29 15:38...|"@SintSonja @Poli...|
|"Fri May 29 15:38...|"RT @narkobars: S...|
|"Fri May 29 15:38...|"@KellyOverCorona...|
|"Fri May 29 15:38...|"@Tobientin Jajas...|
|"Fri May 29 15:38...|"@Timm025 Open dm...|
|"Fri May 29 15:38...|"@Nieuwsblad_be D...|
|"Fri May 29 15:38...|"@OzanKemalOzan @...|
|"Fri May 29 15:38...|"@SQ__D @TorfsBot...|
|"Fri May 29 15:38...|"\ud83c\udfac Maa...|
|"Fri May 29 15:38...|"@ciciloqq hy wel...|
|"Fri May 29 15:38...|"Hercule Poirot  ...|
|"Fri May 29 15:38...|"@gbr8898 @MattHD...|
|"Fri May 29 15:38...|"@FransOldejans A...|
|"Fri May 29 15:38...|"@crypto4all9 @NO...|
|"Fri May 29 15:38...|"jungkook wtf kdj...|
|"Fri May 29 15:38...|"RT @STUDIOdebali...|
|"Fri May 29 15:38...|"like w htklem 3n...|
|"Fri May 29 15:38...|"Andre Rieu Amazi...|
|"Fri May 29 15:38...|"@AdvocaatBoone I...|
|"Fri May 29 15:38...|"@victoria

In [7]:
tokenizer2 = Tokenizer(inputCol="Text", outputCol="words_token")
tokenized = tokenizer2.transform(DF1).select('Date','Text','words_token')
remover = StopWordsRemover(stopWords=["aan","af","al","als","bij","dan","dat","die","dit","een","en","er","had","heb","hem","het","hij","hoe","hun","ik","in","is","je","kan","me","men","met","mij","nog","nu","of","ons","ook","te","tot","uit","van","was","wat","we","wel","wij","zal","ze","zei","zij","zo","zou","aangaande","aangezien","achter","achterna","afgelopen","aldaar","aldus","alhoewel","alias","alle","allebei","alleen","alsnog","altijd","altoos","ander","andere","anders","anderszins","behalve","behoudens","beide","beiden","ben","beneden","bent","bepaald","betreffende","binnen","binnenin","boven","bovenal","bovendien","bovengenoemd","bovenstaand","bovenvermeld","buiten","daar","daarheen","daarin","daarna","daarnet","daarom","daarop","daarvanlangs","de","dikwijls","door","doorgaand","dus","echter","eer","eerdat","eerder","eerlang","eerst","elk","elke","enig","enigszins","enkel","erdoor","even","eveneens","evenwel","gauw","gedurende","geen","gehad","gekund","geleden","gelijk","gemoeten","gemogen","geweest","gewoon","gewoonweg","haar","hadden","hare","hebben","hebt","heeft","hen","hierbeneden","hierboven","hoewel","hunne","ikzelf","inmiddels","inzake","jezelf","jij","jijzelf","jou","jouw","jouwe","juist","jullie","klaar","kon","konden","krachtens","kunnen","kunt","later","liever","maar","mag","meer","mezelf","mijn","mijnent","mijner","mijzelf","misschien","mocht","mochten","moest","moesten","moet","moeten","mogen","na","naar","nadat","net","niet","noch","nogal","ofschoon","om","omdat","omhoog","omlaag","omstreeks","omtrent","omver","onder","ondertussen","ongeveer","onszelf","onze","op","opnieuw","opzij","over","overeind","overigens","pas","precies","reeds","rond","rondom","sedert","sinds","sindsdien","slechts","sommige","spoedig","steeds","tamelijk","tenzij","terwijl","thans","tijdens","toch","toen","toenmaals","toenmalig","totdat","tussen","uitgezonderd","vaakwat","vandaan","vanuit","vanwege","veeleer","verder","vervolgens","vol","volgens","voor","vooraf","vooral","vooralsnog","voorbij","voordat","voordezen","voordien","voorheen","voorop","vooruit","vrij","vroeg","waar","waarom","wanneer","want","waren","weer","weg","wegens","weldra","welk","welke","wie","wiens","wier","wijzelf","zelfs","zichzelf","zijn","zijne","zodra","zonder","zouden","zowat","zulke","zullen","zult","rt","ık","deze","u","via","-",",",'"[full_text": ','"truncated', '"rt',' '], inputCol='words_token', outputCol='words_clean')
data_clean = remover.transform(tokenized).select('Date', 'words_clean')
print('############ Data Cleaning extract:')
data_clean.show()

############ Data Cleaning extract:
+--------------------+--------------------+
|                Date|         words_clean|
+--------------------+--------------------+
|"Fri May 29 15:38...|["@sintsonja, @po...|
|"Fri May 29 15:38...|[@narkobars:, sho...|
|"Fri May 29 15:38...|["@kellyovercoron...|
|"Fri May 29 15:38...|["@tobientin, jaj...|
|"Fri May 29 15:38...|["@timm025, open,...|
|"Fri May 29 15:38...|["@nieuwsblad_be,...|
|"Fri May 29 15:38...|["@ozankemalozan,...|
|"Fri May 29 15:38...|["@sq__d, @torfsb...|
|"Fri May 29 15:38...|["\ud83c\udfac, m...|
|"Fri May 29 15:38...|["@ciciloqq, hy, ...|
|"Fri May 29 15:38...|["hercule, poirot...|
|"Fri May 29 15:38...|["@gbr8898, @matt...|
|"Fri May 29 15:38...|["@fransoldejans,...|
|"Fri May 29 15:38...|["@crypto4all9, @...|
|"Fri May 29 15:38...|["jungkook, wtf, ...|
|"Fri May 29 15:38...|[@studıodebalie:,...|
|"Fri May 29 15:38...|["like, w, htklem...|
|"Fri May 29 15:38...|["andre, rieu, am...|
|"Fri May 29 15:38...|["@advocaatboone,.

In [8]:
result = data_clean.withColumn('words_clean', f.explode(f.col('words_clean'))) \
  .groupBy('words_clean') \
  .count().sort('count', ascending=False) \

print('############')
result.show()

############
+-----------+-----+
|words_clean|count|
+-----------+-----+
|           |  850|
|       gaat|  237|
|     mensen|  222|
|      wordt|  200|
|       goed|  196|
|       echt|  188|
|       veel|  174|
|          1|  166|
|       eens|  162|
|       hier|  147|
|       gaan|  147|
|        wil|  139|
|       heel|  136|
|     worden|  134|
|       iets|  121|
|      tegen|  121|
|         ja|  120|
|       jaar|  120|
|     nieuwe|  118|
|         ın|  113|
+-----------+-----+
only showing top 20 rows

